# VacationPy

In [1]:
# Dependencies and Setup
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import requests
import json
import gmaps
import os

# Import API key
from config import g_key

# Configure gmaps
gmaps.configure(api_key=g_key)


### Store Weather results into DataFrame

In [4]:
# set csv path
weather_df = pd.read_csv("../output_data/weather.csv")

# display dataframe
weather_df.head()


City Hemisphere  Latitude  Longitude  Temperature(F)  Humidity(%)  \
0  Port Keats   southern  -14.2500   129.5500           66.33           48   
1  Abu Samrah   northern   35.3029    37.1841           84.83           33   
2    Saldanha   southern  -33.0117    17.9442           51.85           88   
3       Gouré   northern   13.9835    10.2704           87.10           41   
4   Hay River   northern   60.8156  -115.7999           67.98           60   

   Cloudiness(%)  Wind Speed(mph)  
0             11             8.57  
1              0             9.95  
2            100             8.70  
3             16            11.99  
4             75             8.05

### Humidity Heatmap
* Configure gmaps.
* Use the Lat and Lng as locations and Humidity as the weight.
* Add Heatmap layer to map.

In [5]:
# plot heatmap
fig = gmaps.figure()

# store latitude and longitude in locations
locations = weather_df[["Latitude", "Longitude"]]
humid = weather_df["Humidity(%)"]

# create heat layer
heat_layer = gmaps.heatmap_layer(locations, weights=humid, dissipating=False, max_intensity=101, point_radius=1)

# add layer
fig.add_layer(heat_layer)

# display figure
fig



Figure(layout=FigureLayout(height='420px'))

### Create new DataFrame fitting weather criteria
* Narrow down the cities to fit weather conditions.
* Drop any rows will null values.

In [7]:
# set weather to be greater than 20 and less than 90
ideal_df = weather_df.loc[(weather_df["Temperature(F)"] <= 90) & (weather_df["Temperature(F)"] >= 20),:]

# get rid of rows with null values
ideal_df = ideal_df.dropna(how="any")

# display dataframe
ideal_df


City Hemisphere  Latitude  Longitude  Temperature(F)  \
0         Port Keats   southern  -14.2500   129.5500           66.33   
1         Abu Samrah   northern   35.3029    37.1841           84.83   
2           Saldanha   southern  -33.0117    17.9442           51.85   
3              Gouré   northern   13.9835    10.2704           87.10   
4          Hay River   northern   60.8156  -115.7999           67.98   
..               ...        ...       ...        ...             ...   
551         Sheridan   northern   44.8333  -106.9173           78.66   
552  Plettenberg Bay   southern  -34.0527    23.3716           53.31   
553    Pangkalanbuun   southern   -2.6833   111.6167           73.20   
554     Jacksonville   northern   30.3322   -81.6556           75.33   
555           Tarsus   northern   36.9188    34.8784           80.47   

     Humidity(%)  Cloudiness(%)  Wind Speed(mph)  
0             48             11             8.57  
1             33              0             9.95  
2             88            100             8.70  
3             41             16            11.99  
4             60             75             8.05  
..           ...            ...              ...  
551           31              1             5.75  
552           87            100            11.25  
553           98             91             0.92  
554           89             90             9.22  
555           74              1             3.33  

[512 rows x 8 columns]

### Hotel Map
* Store into variable named `hotel_df`.
* Add a "Hotel Name" column to the DataFrame.
* Set parameters to search for hotels with 5000 meters.
* Hit the Google Places API for each city's coordinates.
* Store the first Hotel result into the DataFrame.
* Plot markers on top of the heatmap.

In [10]:
hotel_df = ideal_df
hotel_df["Hotel Name"] = ""
hotel_df["Country"] = ""
hotel_df["Lat"] = ""
hotel_df["Lng"] = ""


coordinates = []
search = "Hotel"
radius = 5000
places_url = "https://maps.googleapis.com/maps/api/place/nearbysearch/json"
 

for index, row in hotel_df.iterrows():
    lat = row["Latitude"]
    lng = row["Longitude"]
    coordinates = f"{lat}, {lng}"
    params1 = {"location": coordinates,
              "keyword": search,
              "radius": radius,
              "key": g_key}
    response1 = requests.get(places_url, params=params1).json()
    results1  = response1["results"]
    
    try:
        hotel_df.loc[index, "Hotel Name"] = results1[0]["name"]
        hotel_df.loc[index, "Lat"] = float(results1[0]["geometry"]["location"]["lat"])
        hotel_df.loc[index, "Lng"] = float(results1[0]["geometry"]["location"]["lng"])
        hotel_df.loc[index, "Country"] = results1[0]["plus_code"]["global_code"]
    except:
        hotel_df.loc[index, "Hotel Name"] = ""
        hotel_df.loc[index, "Lat"] = ""
        hotel_df.loc[index, "Lng"] = ""
        hotel_df.loc[index, "Country"] = ""
    print(json.dumps(response1, indent=4, sort_keys=True))

hotel_df = hotel_df.loc[hotel_df["Hotel Name"] != "",:]


{
    "error_message": "You must enable Billing on the Google Cloud Project at https://console.cloud.google.com/project/_/billing/enable Learn more at https://developers.google.com/maps/gmp-get-started",
    "html_attributions": [],
    "results": [],
    "status": "REQUEST_DENIED"
}
{
    "html_attributions": [],
    "results": [],
    "status": "ZERO_RESULTS"
}
{
    "error_message": "You must enable Billing on the Google Cloud Project at https://console.cloud.google.com/project/_/billing/enable Learn more at https://developers.google.com/maps/gmp-get-started",
    "html_attributions": [],
    "results": [],
    "status": "REQUEST_DENIED"
}
{
    "html_attributions": [],
    "results": [],
    "status": "ZERO_RESULTS"
}
{
    "error_message": "You must enable Billing on the Google Cloud Project at https://console.cloud.google.com/project/_/billing/enable Learn more at https://developers.google.com/maps/gmp-get-started",
    "html_attributions": [],
    "results": [],
    "status": "R

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 42.110095,
                    "lng": -79.2851245
                },
                "viewport": {
                    "northeast": {
                        "lat": 42.11147222989272,
                        "lng": -79.28182884999998
                    },
                    "southwest": {
                        "lat": 42.10877257010728,
                        "lng": -79.28622305
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "name": "Chautauqua Harbor Hotel",
            "photos": [
                {
                    "height": 1393,
                    "html_attributions": [
                        "<a href=\"https://maps.google.com/maps/contrib/106257334849997488868\">A Google U

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -13.053571,
                    "lng": 33.478038
                },
                "viewport": {
                    "northeast": {
                        "lat": -13.05223447010728,
                        "lng": 33.47908142989272
                    },
                    "southwest": {
                        "lat": -13.05493412989272,
                        "lng": 33.47638177010728
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "name": "Chikho Hotel",
            "opening_hours": {
                "open_now": true
            },
            "photos": [
                {
                    "height": 1536,
                    "html_attributions": [
                        "<a href=

{
    "html_attributions": [],
    "next_page_token": "Aap_uED3yA4553jJuFKPgGjCBkqrSJ2f_qUKrHwlzssCTGow-dL8NwhUB8OYiS6JQF27S9AufERUF-lMJ9X7fnXXSRrL7DSPmWNQeXzAMLvdHHoNckXY6LGKmYGcyPzmGrdVZQToMZIOzPewkbbwendm4-2ojvAT-INhsaoQ62b3oQFC9rguBigkvQBlrxn8NtJTIpa_dX4lJaef-XHit6Fpr7IGZN3T8GA5qrlLfOKu7uEbUguNUH6pcigSGtbhZou6m6PuOn598yoLZIzwOsWJTS5nDOVMkCx53sfXfy-33kQ31Bo8I12E2kGsgCjn3vkkXMq3tUhBuuFT2M8P1MsBKtejUQ7yDhFsdQ0ID8MHP-UNDPFdogbMvM3lbn79pUw_yGkDBvkdle78La5jf7Sh883UgPBBK_F7zo3Qc4XVqAHT6ikA0TXy9w",
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -53.1605535,
                    "lng": -70.9109371
                },
                "viewport": {
                    "northeast": {
                        "lat": -53.15917457010728,
                        "lng": -70.90967042010729
                    },
                    "southwest": {
                        "lat": -53.16187422989272

{
    "error_message": "You must enable Billing on the Google Cloud Project at https://console.cloud.google.com/project/_/billing/enable Learn more at https://developers.google.com/maps/gmp-get-started",
    "html_attributions": [],
    "results": [],
    "status": "REQUEST_DENIED"
}
{
    "html_attributions": [],
    "next_page_token": "Aap_uEBPnxWKthpPOYbMyTvrGX9J0zA4zAm41lC-VW5YncdQILh5mFmAkT_EuBaD7l6QRrQGfaX-fJLV7FTIhHOKnDrNIlUOpouX7iCk71P8CIgu-JcxZiar4TZ1uVqJT6NKdVFg0xZQe8ZxDhp8jRKIOLDQhfaW5HIMoWgJL42ukNbOXERffVdqCvBkCkIcqn5w85cvXGBa0C_JQnwATRUr4ieS9vYNF_DsoWdhpmZmfQtt36X1PllCvH9wE6GlawflNVvXc_yCijW_NAmAMfWeCg_odWwQuLrdsq2Oo0-ywQpQXRO1JAZu31rZOxkHqhT2ZX3ytR633NAUR1YajJ42JbuOLcDgcRMzrDfpAkmm9t32BpGWtkpGzAartUg1TsFH4C9i-JKjCNKUyyMy_7HDLpA4l-ZwrOmsLldvWr8T76NJ2wBKAlZRRw",
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -32.9834715,
                    "lng": 27.9510976
        

...

{
    "html_attributions": [],
    "next_page_token": "Aap_uEDibCwNBMhb7q93ORvkV3g4D5te6jo3_JK9clnOVh9_LIKEXSIyrPoYImGnYjucAZABDHC2c2_Gbf68Y3QF7dJTzKHBWdq73P-_8em3eSWueNBSRq_yC2-m_kiy6teXayjfK8MJW7vlelH8vovt82Rel62GAoJKmCTOetfWevLA_8gqeMolKkjpBFhsEyojv95vbmfhEzmK046SoNmqZg4S6gLjRl6tSGtJ1nbs1RWk3Xc-8rnTUvU9WFSdoFuKjAJTi8BQg_NTrHzABxbxYRHDBcCwyrtO-qD-5D3vuz5W9oizsQ-wlKoAxJNbKg73_r00uHHAsiUCDAYfDGhhzp-shkzyvlQjwVdBLF4c4nUc18SNcEwkc799STX8QBJDjks-WlRpaQTYGEru1ev79XRidI9Ol0PpOqHHq3k3yKLNPWUD2SYLuQ",
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -22.570407,
                    "lng": 17.085683
                },
                "viewport": {
                    "northeast": {
                        "lat": -22.56900167010727,
                        "lng": 17.08716232989272
                    },
                    "southwest": {
                        "lat": -22.57170132989272,
  

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 44.8064768,
                    "lng": -106.9539187
                },
                "viewport": {
                    "northeast": {
                        "lat": 44.80785122989273,
                        "lng": -106.9522792201073
                    },
                    "southwest": {
                        "lat": 44.80515157010728,
                        "lng": -106.9549788798927
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "name": "Sheridan Inn",
            "opening_hours": {
                "open_now": true
            },
            "photos": [
                {
                    "height": 3306,
                    "html_attributions": [
                        "<a hr

{
    "html_attributions": [],
    "next_page_token": "Aap_uECzhN8UP6lqjA8X48QPHWTVyfOfGyUqB1ibPFMEAkUG1_plxRGWOtJ7PKRQI196bo9J6g9svo7YYfHjMCRRPpFHSF3VKJjS57ASH8N-T-JQ-LDWyD-bWovZT4bnpKNlIZViswOG-wpJqddU0sa5QEaR3TOBCJ6fN1NIYQwAhgJMYNRajMm7q4QFXE8Os8tCvAzgBHLmobrpd4-BTSBaqee1-9RzETk67f8wC6Zg69CSVlBUJ-KzOnmSPr14nW2PPXobz0KBYBsv6DoYQHhgmNmcCDQzmo2ZH3KgG29Fied-aRrQiL20jl75r4_9wga09hUrZwBY-qhLAMwlyvGMUEuvTBBZ5I0aiH8HrHP4hrh-U0KYAugD70weWXEKC1syVkTWpS_Xeijgigjn6p4IFJtAceJwnycTRV-1YljOzLy0jr0n62TD2g",
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -34.05381,
                    "lng": 23.37756
                },
                "viewport": {
                    "northeast": {
                        "lat": -34.05257927010728,
                        "lng": 23.37890677989272
                    },
                    "southwest": {
                        "lat": -34.05527892989272,
    

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 30.3259472,
                    "lng": -81.6618889
                },
                "viewport": {
                    "northeast": {
                        "lat": 30.32798655,
                        "lng": -81.65965994999999
                    },
                    "southwest": {
                        "lat": 30.32444315,
                        "lng": -81.66442294999999
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "name": "Omni Jacksonville Hotel",
            "opening_hours": {
                "open_now": true
            },
            "photos": [
                {
                    "height": 660,
                    "html_attributions": [
                        "<a href=

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 36.917108,
                    "lng": 34.8958159
                },
                "viewport": {
                    "northeast": {
                        "lat": 36.91845822989271,
                        "lng": 34.89716662989272
                    },
                    "southwest": {
                        "lat": 36.91575857010727,
                        "lng": 34.89446697010728
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "name": "Otel Zorbaz",
            "opening_hours": {
                "open_now": true
            },
            "photos": [
                {
                    "height": 540,
                    "html_attributions": [
                        "<a href=\"ht

In [7]:
#get countries

geocode_url = "https://maps.googleapis.com/maps/api/geocode/json?"

for index, row in hotel_df.iterrows():
    global_code = row["Country"]
    params2 = {"address": global_code, 
               "key": g_key}
    try:
        response2 = requests.get(geocode_url, params=params2).json()
        hotel_df.loc[index, "Country"] = response2["results"][0]["address_components"][4]["long_name"]
    except:
        hotel_df.loc[index, "Country"] = ""


In [8]:
hotel_df = hotel_df.loc[hotel_df["Country"] != "",:]
hotel_df.head(400)

City Hemisphere  Latitude  Longitude  Temperature(F)  \
59           Hobart   southern  -42.8794   147.3294           47.46   
122    Port Lincoln   southern  -34.7333   135.8667           69.51   
124          Burnie   southern  -41.0667   145.9167           51.17   
173    Ponta do Sol   northern   32.6667   -17.1000           57.22   
179  Ribeira Grande   northern   38.5167   -28.7000           62.60   
184       Tocopilla   southern  -22.0920   -70.1979           73.58   
210         Camacha   northern   33.0833   -16.3333           62.60   
264    Constitución   southern  -35.3333   -72.4167           70.18   
274           Rocha   southern  -34.4833   -54.3333           70.61   
315           Ancud   southern  -41.8697   -73.8203           79.20   
353        Coquimbo   southern  -29.9533   -71.3436           68.00   
381          Taltal   southern  -25.4000   -70.4833           70.39   
475        Barcelos   northern   41.5388    -8.6151           50.67   
515          Lukang   northern   24.0567   120.4352           61.66   

     Humidity(%)  Cloudiness(%)  Wind Speed(mph)  \
59            81             40             5.75   
122           61              0             7.87   
124           78             29            11.74   
173           64             95             3.00   
179           94             75            24.16   
184           57             34             5.97   
210           82             20            10.36   
264           65             11             8.14   
274           82             52            15.17   
315           41              0             9.22   
353           68              0            14.97   
381           63             30             7.27   
475           76             75            13.80   
515           88             40             2.77   

                           Hotel Name            Country      Lat      Lng  
59      Hotel Grand Chancellor Hobart       Kaw Township -42.8809  147.334  
122                Port Lincoln Hotel      Harris County -34.7178  135.854  
124      Beachfront Voyager Motor Inn           Arkansas -41.0503  145.907  
173                    Hotel do Campo      United States   32.677 -17.0661  
179            Quinta Das Buganvílias             Oregon  38.5222 -28.7105  
184             Entre Fuentes Y Lagos              Chile -22.0862 -70.1939  
210           Hotel Porto Santo & Spa             Kansas  33.0506 -16.3468  
264            Hotel Casona del Cerro            Georgia -35.3378  -72.418  
274                      Casa Rodo 53         Tamaulipas -34.4835 -54.3358  
315          Panamericana Hotel Ancud     Garland County -41.8624 -73.8301  
353  Enjoy Coquimbo Hotel de la Bahía              Chile -29.9473 -71.2912  
381                    Hostal Beatriz              Chile -25.4076 -70.4798  
475  In Barcelos Hostel & Guest House  Brooking Township  41.5297 -8.62165  
515                   鹿港鉑鈳民宿-Back Inn             Kansas  24.0563  120.437

In [9]:
# NOTE: Do not change any of the code in this cell

# Using the template add the hotel marks to the heatmap
info_box_template = """
<dl>
<dt>Name</dt><dd>{Hotel Name}</dd>
<dt>City</dt><dd>{City}</dd>
<dt>Country</dt><dd>{Country}</dd>
</dl>
"""
# Store the DataFrame Row
# NOTE: be sure to update with your DataFrame name
hotel_info = [info_box_template.format(**row) for index, row in hotel_df.iterrows()]
locations = hotel_df[["Lat", "Lng"]]

In [10]:
# Add marker layer ontop of heat map
markers = gmaps.marker_layer(locations, info_box_content = hotel_info)
fig.add_layer(markers)

# Display figure
fig

Figure(layout=FigureLayout(height='420px'))